In [1]:
from sklearn import datasets
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd 
import folium
from folium import plugins
import geopandas as gpd
from bokeh.io import output_notebook, show, output_file
from bokeh.plotting import figure
from bokeh.models import GeoJSONDataSource, LogColorMapper, ColorBar
from bokeh.palettes import YlOrRd
import json

In [2]:
shapefile = '../data/geo_data/ne_110m_admin_0_countries.shp'
#Read shapefile using Geopandas
gdf = gpd.read_file(shapefile)[['ADMIN', 'ADM0_A3', 'geometry']]
#Rename columns.
gdf.columns = ['country', 'country_code', 'geometry']
gdf = gdf.drop(gdf.index[159]) #remove antartica
gdf.head()

country country_code  \
0                         Fiji          FJI   
1  United Republic of Tanzania          TZA   
2               Western Sahara          SAH   
3                       Canada          CAN   
4     United States of America          USA   

                                            geometry  
0  MULTIPOLYGON (((180.00000 -16.06713, 180.00000...  
1  POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...  
2  POLYGON ((-8.66559 27.65643, -8.66512 27.58948...  
3  MULTIPOLYGON (((-122.84000 49.00000, -122.9742...  
4  MULTIPOLYGON (((-122.84000 49.00000, -120.0000...

In [3]:
gpd.read_file(shapefile)

featurecla  scalerank  LABELRANK                        SOVEREIGNT  \
0    Admin-0 country          1          6                              Fiji   
1    Admin-0 country          1          3       United Republic of Tanzania   
2    Admin-0 country          1          7                    Western Sahara   
3    Admin-0 country          1          2                            Canada   
4    Admin-0 country          1          2          United States of America   
5    Admin-0 country          1          3                        Kazakhstan   
6    Admin-0 country          1          3                        Uzbekistan   
7    Admin-0 country          1          2                  Papua New Guinea   
8    Admin-0 country          1          2                         Indonesia   
9    Admin-0 country          1          2                         Argentina   
10   Admin-0 country          1          2                             Chile   
11   Admin-0 country          1          2  Democratic Republic of the Congo   
12   Admin-0 country          1          6                           Somalia   
13   Admin-0 country          1          2                             Kenya   
14   Admin-0 country          1          3                             Sudan   
15   Admin-0 country          1          3                              Chad   
16   Admin-0 country          1          5                             Haiti   
17   Admin-0 country          1          5                Dominican Republic   
18   Admin-0 country          1          2                            Russia   
19   Admin-0 country          1          4                       The Bahamas   
20   Admin-0 country          1          5                    United Kingdom   
21   Admin-0 country          1          3                            Norway   
22   Admin-0 country          1          3                           Denmark   
23   Admin-0 country          3          6                            France   
24   Admin-0 country          1          5                        East Timor   
25   Admin-0 country          1          2                      South Africa   
26   Admin-0 country          1          6                           Lesotho   
27   Admin-0 country          1          2                            Mexico   
28   Admin-0 country          1          4                           Uruguay   
29   Admin-0 country          1          2                            Brazil   
..               ...        ...        ...                               ...   
147  Admin-0 country          1          2                       Philippines   
148  Admin-0 country          1          3                          Malaysia   
149  Admin-0 country          1          6                            Brunei   
150  Admin-0 country          1          6                          Slovenia   
151  Admin-0 country          1          3                           Finland   
152  Admin-0 country          1          6                          Slovakia   
153  Admin-0 country          1          5                           Czechia   
154  Admin-0 country          1          4                           Eritrea   
155  Admin-0 country          1          2                             Japan   
156  Admin-0 country          1          4                          Paraguay   
157  Admin-0 country          1          3                             Yemen   
158  Admin-0 country          1          2                      Saudi Arabia   
159  Admin-0 country          1          4                        Antarctica   
160  Admin-0 country          1          6                   Northern Cyprus   
161  Admin-0 country          1          5                            Cyprus   
162  Admin-0 country          1          3                           Morocco   
163  Admin-0 country          1          2                             Egypt   
164  Admin-0 country          1          3                             Libya   
165  Admin

In [4]:
datafile = '../data/time_series_covid19_deaths_global_iso3_regions.csv'
#Read csv file using pandas
df = pd.read_csv(datafile)
df

Province/State          Country/Region  \
0                          #adm1+name           #country+name   
1                                 NaN             Afghanistan   
2                                 NaN                 Albania   
3                                 NaN                 Algeria   
4                                 NaN                 Andorra   
5                                 NaN                  Angola   
6                                 NaN     Antigua and Barbuda   
7                                 NaN               Argentina   
8                                 NaN                 Armenia   
9        Australian Capital Territory               Australia   
10                    New South Wales               Australia   
11                 Northern Territory               Australia   
12                         Queensland               Australia   
13                    South Australia               Australia   
14                           Tasmania               Australia   
15                           Victoria               Australia   
16                  Western Australia               Australia   
17                                NaN                 Austria   
18                                NaN              Azerbaijan   
19                                NaN                 Bahamas   
20                                NaN                 Bahrain   
21                                NaN              Bangladesh   
22                                NaN                Barbados   
23                                NaN                 Belarus   
24                                NaN                 Belgium   
25                                NaN                   Benin   
26                                NaN                  Bhutan   
27                                NaN                 Bolivia   
28                                NaN  Bosnia and Herzegovina   
29                                NaN                  Brazil   
..                                ...                     ...   
235                               NaN              Mozambique   
236                               NaN                   Syria   
237                               NaN             Timor-Leste   
238                               NaN                  Belize   
239                         Recovered                  Canada   
240                               NaN                    Laos   
241                               NaN                   Libya   
242                               NaN      West Bank and Gaza   
243                               NaN           Guinea-Bissau   
244                               NaN                    Mali   
245                               NaN   Saint Kitts and Nevis   
246             Northwest Territories                  Canada   
247                             Yukon                  Canada   
248                               NaN                  Kosovo   
249                               NaN                   Burma   
250                          Anguilla          United Kingdom   
251            British Virgin Islands          United Kingdom   
252          Turks and Caicos Islands          United Kingdom   
253                               NaN              MS Zaandam   
254                               NaN                Botswana   
255                               NaN                 Burundi   
256                               NaN            Sierra Leone   
257  Bonaire, Sint Eustatius and Saba             Netherlands   
258                               NaN                  Malawi   
259       Falkland Islands (Malvinas)          United Kingdom   
260         Saint Pierre and Miquelon                  France   
261                               NaN             South Sudan   
262                               NaN          Western Sahara   
263                               NaN   Sao Tome and Principe   
264                               NaN                   Ye

In [5]:
 df.groupby(['ISO 3166-1 Alpha 3-Codes']).sum().reset_index().head()

ISO 3166-1 Alpha 3-Codes  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  \
0            #country+code      0.0      0.0      0.0      0.0      0.0   
1                      ABW      0.0      0.0      0.0      0.0      0.0   
2                      AFG      0.0      0.0      0.0      0.0      0.0   
3                      AGO      0.0      0.0      0.0      0.0      0.0   
4                      AIA      0.0      0.0      0.0      0.0      0.0   

   1/27/20  1/28/20  1/29/20  1/30/20  ...  4/14/20  4/15/20  4/16/20  \
0      0.0      0.0      0.0      0.0  ...      0.0      0.0      0.0   
1      0.0      0.0      0.0      0.0  ...      0.0      1.0      2.0   
2      0.0      0.0      0.0      0.0  ...     23.0     25.0     30.0   
3      0.0      0.0      0.0      0.0  ...      2.0      2.0      2.0   
4      0.0      0.0      0.0      0.0  ...      0.0      0.0      0.0   

   4/17/20  4/18/20  4/19/20  4/20/20  4/21/20  4/22/20  4/23/20  
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
1      2.0      2.0      2.0      2.0      2.0      2.0      2.0  
2     30.0     30.0     33.0     36.0     36.0     40.0     42.0  
3      2.0      2.0      2.0      2.0      2.0      2.0      2.0  
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0  

[5 rows x 94 columns]

In [6]:
 df.groupby(['ISO 3166-1 Alpha 3-Codes']).sum().reset_index()
country_total = df.groupby(['ISO 3166-1 Alpha 3-Codes']).sum().iloc[:,-1]
country_total = pd.DataFrame(country_total).reset_index()

In [7]:
country_total.head()

ISO 3166-1 Alpha 3-Codes  4/23/20
0            #country+code      0.0
1                      ABW      2.0
2                      AFG     42.0
3                      AGO      2.0
4                      AIA      0.0

In [8]:
now = '4/23/20'
df_newest = pd.DataFrame(country_total[['ISO 3166-1 Alpha 3-Codes', now]])
df_newest.columns = ['country_code', 'deaths']
df_newest = df_newest.drop(0)

In [9]:
df_newest.head()

country_code  deaths
1          ABW     2.0
2          AFG    42.0
3          AGO     2.0
4          AIA     0.0
5          ALB    27.0

In [10]:
merged = gdf.merge(df_newest, on = 'country_code')
merged.head()

country country_code  \
0                         Fiji          FJI   
1  United Republic of Tanzania          TZA   
2                       Canada          CAN   
3     United States of America          USA   
4                   Kazakhstan          KAZ   

                                            geometry   deaths  
0  MULTIPOLYGON (((180.00000 -16.06713, 180.00000...      0.0  
1  POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...     10.0  
2  MULTIPOLYGON (((-122.84000 49.00000, -122.9742...   2240.0  
3  MULTIPOLYGON (((-122.84000 49.00000, -120.0000...  49954.0  
4  POLYGON ((87.35997 49.21498, 86.59878 48.54918...     20.0

In [11]:
merged[merged['country'] == 'Kazakhstan']

country country_code                                           geometry  \
4  Kazakhstan          KAZ  POLYGON ((87.35997 49.21498, 86.59878 48.54918...   

   deaths  
4    20.0

In [12]:
#Read data to json.
merged_json = json.loads(merged.to_json())
#Convert to String like object.
json_data = json.dumps(merged_json)

In [13]:
country_total = df.groupby(['ISO 3166-1 Alpha 3-Codes']).sum().reset_index()


In [14]:
def json_data(data, mergeOn):
    merged = gdf.merge(data, left_on = 'country_code', right_on = mergeOn, how = 'left')
    merged.fillna('No data', inplace = True)
    merged['selected'] = merged['4/23/20']
    merged_json = json.loads(merged.to_json())
    json_data = json.dumps(merged_json)
    return json_data

In [76]:
from bokeh.io import curdoc, output_notebook
from bokeh.models import HoverTool, LogTicker, BasicTickFormatter
from datetime import date
import colorcet as cc


#Input GeoJSON source that contains features for plotting.
geosource = GeoJSONDataSource(geojson = json_data(country_total,'ISO 3166-1 Alpha 3-Codes'))
#Define a sequential multi-hue color palette.
palette = cc.fire[:-25]
#Reverse color order 
palette = palette[::-1]


#The reason for not setting low = 0 is that we are using log scale and log(0) is undefined and this causes problems in
#the colorbar
color_mapper = LogColorMapper(palette = palette, low = 1, high = 5e6, low_color = '#fff0ba', nan_color = '#d9d9d9')
#Define custom tick labels for color bar.


#Add hover tool
hover = HoverTool(tooltips = [ ('Country','@country'),('Deaths', '@selected')])

#Add colorbar
color_bar = ColorBar(color_mapper=color_mapper, ticker=LogTicker(),
                     label_standoff=12, border_line_color=None, location=(0,0), 
                     formatter = BasicTickFormatter(power_limit_high = 10))

#Create figure object.
p = figure(title = 'Death count', plot_height = 400 , plot_width = 800, toolbar_location = 'above', tools = [hover,"pan,wheel_zoom","box_zoom", "reset"])
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
p.axis.visible = False
p.add_layout(color_bar, 'right')
#Add patch renderer to figure. 
p.patches('xs','ys', source = geosource,fill_color = {'field' :'selected', 'transform' : color_mapper},
          line_color = 'black', line_width = 0.25, fill_alpha = 1)

GlyphRenderer(id='8820', ...)

Visualization showed an error in Kazakhstan because 20/3 there are registered 3 dead but 21/3 there are registered 0 dead. Looking at other sources (https://www.worldometers.info/coronavirus/country/kazakhstan/ and https://en.wikipedia.org/wiki/2020_coronavirus_pandemic_in_Kazakhstan) this seems to be an error and the number should be 0 20/3.

## Add countermeasures

In [77]:
countermeasures_file = '../data/OxCGRT_Download_270420_180204_Full.csv'
#Read csv file using pandas
countermeasures = pd.read_csv(countermeasures_file)

In [78]:
countermeasures.columns = countermeasures.columns.str.replace(' ', '_')
def convertDate(date): 
    # convert 20200122 into 1/22/20
    s = str(date)
    year = s[2:4]
    month = s[5:6]
    day = str(int(s[6:8]))
    return month + '/' + day + '/' + year

countermeasures['Date'] = countermeasures['Date'].apply(convertDate)

In [79]:
countermeasures.head()

CountryName CountryCode    Date  S1_School_closing  S1_IsGeneral S1_Notes  \
0       Aruba         ABW  1/1/20                0.0           NaN      NaN   
1       Aruba         ABW  1/2/20                0.0           NaN      NaN   
2       Aruba         ABW  1/3/20                0.0           NaN      NaN   
3       Aruba         ABW  1/4/20                0.0           NaN      NaN   
4       Aruba         ABW  1/5/20                0.0           NaN      NaN   

   S2_Workplace_closing  S2_IsGeneral S2_Notes  S3_Cancel_public_events  ...  \
0                   0.0           NaN      NaN                      0.0  ...   
1                   0.0           NaN      NaN                      0.0  ...   
2                   0.0           NaN      NaN                      0.0  ...   
3                   0.0           NaN      NaN                      0.0  ...   
4                   0.0           NaN      NaN                      0.0  ...   

   S11_Notes S12_Testing_framework  S12_Notes  S13_Contact_tracing S13_Notes  \
0        NaN                   0.0        NaN                  0.0       NaN   
1        NaN                   0.0        NaN                  0.0       NaN   
2        NaN                   0.0        NaN                  0.0       NaN   
3        NaN                   0.0        NaN                  0.0       NaN   
4        NaN                   0.0        NaN                  0.0       NaN   

   ConfirmedCases  ConfirmedDeaths StringencyIndex  StringencyIndexForDisplay  \
0             NaN              NaN             0.0                        0.0   
1             NaN              NaN             0.0                        0.0   
2             NaN              NaN             0.0                        0.0   
3             NaN              NaN             0.0                        0.0   
4             NaN              NaN             0.0                        0.0   

   Unnamed:_39  
0           \t  
1           \t  
2           \t  
3           \t  
4           \t  

[5 rows x 40 columns]

In [80]:
countermeasures.columns

Index(['CountryName', 'CountryCode', 'Date', 'S1_School_closing',
       'S1_IsGeneral', 'S1_Notes', 'S2_Workplace_closing', 'S2_IsGeneral',
       'S2_Notes', 'S3_Cancel_public_events', 'S3_IsGeneral', 'S3_Notes',
       'S4_Close_public_transport', 'S4_IsGeneral', 'S4_Notes',
       'S5_Public_information_campaigns', 'S5_IsGeneral', 'S5_Notes',
       'S6_Restrictions_on_internal_movement', 'S6_IsGeneral', 'S6_Notes',
       'S7_International_travel_controls', 'S7_Notes', 'S8_Fiscal_measures',
       'S8_Notes', 'S9_Monetary_measures', 'S9_Notes',
       'S10_Emergency_investment_in_health_care', 'S10_Notes',
       'S11_Investment_in_Vaccines', 'S11_Notes', 'S12_Testing_framework',
       'S12_Notes', 'S13_Contact_tracing', 'S13_Notes', 'ConfirmedCases',
       'ConfirmedDeaths', 'StringencyIndex', 'StringencyIndexForDisplay',
       'Unnamed:_39'],
      dtype='object')

2.0

In [82]:
school_countermeasures = countermeasures[['CountryCode', 'Date', 'S1_School_closing']]
school_countermeasures = school_countermeasures.set_index(['CountryCode', 'Date']).S1_School_closing.unstack()


In [83]:
workplace_countermeasures = countermeasures[['CountryCode', 'Date', 'S2_Workplace_closing']]
workplace_countermeasures = workplace_countermeasures.set_index(['CountryCode', 'Date']).S2_Workplace_closing.unstack().reset_index()


In [84]:
public_events_countermeasures = countermeasures[['CountryCode', 'Date', 'S3_Cancel_public_events']]
public_events_countermeasures = public_events_countermeasures.set_index(['CountryCode', 'Date']).S3_Cancel_public_events.unstack().reset_index()


In [85]:
public_transport_countermeasures = countermeasures[['CountryCode', 'Date', 'S4_Close_public_transport']]
public_transport_countermeasures = public_transport_countermeasures.set_index(['CountryCode', 'Date']).S4_Close_public_transport.unstack().reset_index()


In [86]:
travel_countermeasures = countermeasures[['CountryCode', 'Date', 'S7_International_travel_controls']]
travel_countermeasures = travel_countermeasures.set_index(['CountryCode', 'Date']).S7_International_travel_controls.unstack().reset_index()


In [87]:
workplace_countermeasures.head()

Date CountryCode  1/1/20  1/10/20  1/11/20  1/12/20  1/13/20  1/14/20  \
0            ABW     0.0      0.0      0.0      0.0      0.0      0.0   
1            AFG     0.0      0.0      0.0      0.0      0.0      0.0   
2            AGO     0.0      0.0      0.0      0.0      0.0      0.0   
3            ALB     0.0      0.0      0.0      0.0      0.0      0.0   
4            AND     0.0      0.0      0.0      0.0      0.0      0.0   

Date  1/15/20  1/16/20  1/17/20  ...  4/22/20  4/23/20  4/24/20  4/3/20  \
0         0.0      0.0      0.0  ...      2.0      2.0      2.0     2.0   
1         0.0      0.0      0.0  ...      NaN      NaN      NaN     2.0   
2         0.0      0.0      0.0  ...      NaN      NaN      NaN     2.0   
3         0.0      0.0      0.0  ...      NaN      NaN      NaN     2.0   
4         0.0      0.0      0.0  ...      2.0      NaN      NaN     2.0   

Date  4/4/20  4/5/20  4/6/20  4/7/20  4/8/20  4/9/20  
0        2.0     2.0     2.0     2.0     2.0     2.0  
1        2.0     2.0     2.0     2.0     2.0     2.0  
2        2.0     2.0     2.0     2.0     2.0     2.0  
3        2.0     2.0     2.0     2.0     2.0     2.0  
4        2.0     2.0     2.0     2.0     2.0     2.0  

[5 rows x 116 columns]

In [133]:
#Input GeoJSON source that contains features for plotting.
school_geosource = GeoJSONDataSource(geojson = json_data(school_countermeasures,'CountryCode'))
work_geosource = GeoJSONDataSource(geojson = json_data(workplace_countermeasures,'CountryCode'))
public_events_geosource = GeoJSONDataSource(geojson = json_data(public_events_countermeasures,'CountryCode'))
public_transport_geosource = GeoJSONDataSource(geojson = json_data(public_transport_countermeasures,'CountryCode'))
travel_geosource = GeoJSONDataSource(geojson = json_data(travel_countermeasures,'CountryCode'))
countermeasures_geosource = GeoJSONDataSource(geojson = json_data(workplace_countermeasures,'CountryCode'))

In [225]:
from bokeh.io import curdoc, output_notebook
from bokeh.models import HoverTool, LogTicker, BasicTickFormatter, LinearColorMapper, CategoricalColorMapper,FixedTicker, FuncTickFormatter,CustomJSHover
from datetime import date
from bokeh.palettes import Oranges



#Define a sequential multi-hue color palette.
palette = Oranges[4]
#Reverse color order 
palette = palette[::-1]


#The reason for not setting low = 0 is that we are using log scale and log(0) is undefined and this causes problems in
#the colorbar
countermeasures_color_mapper = LinearColorMapper(palette = palette, low = 0, high = 4, nan_color = '#d9d9d9')
#Define custom tick labels for color bar.

#countermeasures_color_mapper = CategoricalColorMapper(factors=['0', '1', '2', '3'], palette=palette)
def formatter(n):
    print(n)
    if (n == 0):
        return 'None'
    else:
        return 'Some'
#Add hover tool
hover_formatter = CustomJSHover(code="""
    if (value == 0){
        return 'No measures / No restrictions'
    } if (value == 1) {
        return 'Recommendations only or mild restrictions'
    } if (value == 2) {
        return 'High restrictions'
    } if (value == 3) {
        return 'Severe restrictions'
    }
""")
countermeasures_hover = HoverTool(tooltips = [ ('Country','@country'),
                                              ('Severity of restrictions ', '@selected{custom}')],
    formatters={'@selected':hover_formatter})



#Add colorbar

ticker = FixedTicker(ticks=[0.5,1.5,2.5,3.5])
formatter = FuncTickFormatter(code="""
    function(tick) {
        data = {0.5: 'None', 1.5: 'Low', 2.5: 'Medium', 3.5: 'High'}
        return data[tick]
    }
    """)
tick_labels = {'0.5': 'None', '1.5': 'Low', '2.5':'Medium', '3.5':'High'}
countermeasures_color_bar = ColorBar(color_mapper=countermeasures_color_mapper,ticker=ticker,
                     label_standoff=12, border_line_color=None, location=(0,0), major_label_overrides = tick_labels)

#Create figure object.
countermeasures_p = figure(title = 'Countermeasures', plot_height = 400 , plot_width = 800, toolbar_location = 'above', tools = [countermeasures_hover,"pan,wheel_zoom","box_zoom", "reset"])
countermeasures_p.xgrid.grid_line_color = None
countermeasures_p.ygrid.grid_line_color = None
countermeasures_p.axis.visible = False
countermeasures_p.add_layout(countermeasures_color_bar, 'right')
#Add patch renderer to figure. 
countermeasures_p.patches('xs','ys', source = countermeasures_geosource,fill_color = {'field' :'selected', 'transform' : countermeasures_color_mapper},
          line_color = 'black', line_width = 0.25, fill_alpha = 1)


GlyphRenderer(id='36135', ...)

In [226]:
from bokeh.models import DateSlider, CustomJS

update_map = CustomJS(args=dict(source=geosource, countermeasures_source = countermeasures_geosource), code="""
    var d = new Date(cb_obj.value);
    var day = d.getDate()
    var month = d.getMonth()+1
    var date = month + '/' + day + '/20'
    
    d = source.attributes.data
    d['selected'] = d[date]
    source.attributes.data = d
    
    source.change.emit();
    
    d = countermeasures_source.attributes.data
    d['selected'] = d[date]
    countermeasures_source.attributes.data = d
    
    countermeasures_source.change.emit();
""")
    
# Make a slider object: slider 
slider = DateSlider(title = 'Date',start=date(2020, 1, 22), end=date(2020, 4, 23),
                    value=date(2020, 4, 23), step = 1, width=p.plot_width-100)
slider.callback_policy = "mouseup"
slider.js_on_change('value', update_map)


In [227]:
from bokeh.models.widgets import Button, TableColumn, Toggle
# Set up Play/Pause button/toggle JS
toggle_js = CustomJS(args=dict(slider=slider),code="""
    var update = function(index){
        var slider_date = new Date(slider.value);
        const max = 1587600000000;
        const min = 1579651200000;
        const max_date = new Date(2020,3,23);
        const min_date = new Date(2020,0,22);
        var toggle_val = cb_obj.active;
        if(toggle_val == false) {
            cb_obj.label = '► Play';
            clearInterval(interval);
            } 
        else if (slider_date >= max_date) {
            var new_date = min_date;
            slider.value = new_date.valueOf() 
        }else{
            var new_date = slider_date.setDate(slider_date.getDate() + 1);
            slider.value = new_date.valueOf() 
        }        
    }
    if(cb_obj.active == false){
        cb_obj.label = '► Play';
    }
    else {
        cb_obj.label = '❚❚ Pause';
        var interval = setInterval(update, 500);
    };
""")

toggle_button = Toggle(label='► Play',active=False)
toggle_button.js_on_change('active',toggle_js)


In [228]:
callback = CustomJS(args=dict(p=p, source=countermeasures_geosource, 
                              school_geosource=school_geosource,
                              work_geosource = work_geosource,
                              public_events_geosource = public_events_geosource,
                              public_transport_geosource = public_transport_geosource,
                              travel_geosource = travel_geosource
                             ), code="""

            var selected = cb_obj.active;
            console.log(selected)
            if (selected == 0) {
                source.attributes.data = school_geosource.attributes.data
                source.change.emit();
            } else if (selected == 1) {
                source.attributes.data = work_geosource.attributes.data
                source.change.emit();
            } else if (selected == 2) {
                source.attributes.data = public_events_geosource.attributes.data
                source.change.emit();
            } else if (selected == 3) {
                source.attributes.data = public_transport_geosource.attributes.data
                source.change.emit();
            } else if (selected == 4) {
                source.attributes.data = travel_geosource.attributes.data
                source.change.emit();
            }
            
            
        """)

from bokeh.models.widgets import RadioButtonGroup
radio_button_group = RadioButtonGroup(labels=['Scool Closures', 'Workplace Closures', 'Cancellation of Public Events',
                                             'Public Transport Closures', 'International Travel Restrictions'], 
                                      active=1, callback=callback)


In [229]:
from bokeh.layouts import widgetbox, row, column
# Make a column layout of widgetbox(slider) and plot, and add it to the current document
layout = column(p,widgetbox(slider, toggle_button,(widgetbox(radio_button_group))), countermeasures_p)
curdoc().add_root(layout)
#Display plot inline in Jupyter notebook
output_notebook()
output_file("./bokeh/map.html")
#Display plot
show(layout)

Loading BokehJS ...